<a href="https://colab.research.google.com/github/ImAliMoussa/Tensorflow-Speech-Recognition-Challenge/blob/main/Testing_and_Evaluation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
! pip install -q tensorflow-io
import tensorflow as tf
import tensorflow_io as tfio
from tensorflow import keras
import numpy as np
import os
import random
import tensorflow as tf
from tensorflow.keras import Model
from tensorflow.keras.layers import *
from tensorflow.keras import optimizers
from tensorflow.keras import losses
from tensorflow.keras import metrics
import librosa
import librosa.display
from tensorflow import keras


     |████████████████████████████████| 22.3MB 134kB/s 


In [ ]:
from google.colab import files
files.upload()
! mkdir ~/.kaggle
! cp kaggle.json ~/.kaggle

! chmod 600 ~/.kaggle/kaggle.json
! kaggle competitions download -c tensorflow-speech-recognition-challenge

Saving kaggle.json to kaggle.json
  0% 0.00/501k [00:00<?, ?B/s]
100% 501k/501k [00:00<00:00, 34.1MB/s]
 99% 1.03G/1.04G [00:18<00:00, 72.3MB/s]
100% 1.04G/1.04G [00:18<00:00, 59.4MB/s]
 99% 2.45G/2.46G [00:51<00:00, 38.4MB/s]
100% 2.46G/2.46G [00:51<00:00, 51.7MB/s]
  0% 0.00/50.0 [00:00<?, ?B/s]
100% 50.0/50.0 [00:00<00:00, 44.3kB/s]


In [ ]:
! mkdir /kaggle
! mkdir /kaggle/working
%cd /content
! rm -rf /kaggle/working/train
! 7z x train.7z -o/kaggle/working/
! ls

/content

7-Zip [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,2 CPUs Intel(R) Xeon(R) CPU @ 2.30GHz (306F0),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 1121103842 bytes (1070 MiB)

Extracting archive: train.7z
--
Path = train.7z
Type = 7z
Physical Size = 1121103842
Headers Size = 389133
Method = Delta LZMA2:24
Solid = +
Blocks = 2

  0%      0% 39 - train/audio/_background_noise_/dude_miaowing.wav                                                            0% 41 - train/audio/_background_noise_/pink_noise.wav                                                         0% 54 - train/audio/bed/014f9f65_nohash_0.wav

In [ ]:
%cd /content
! 7z x sample_submission.7z -o./


/content

7-Zip [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,2 CPUs Intel(R) Xeon(R) CPU @ 2.30GHz (306F0),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 512684 bytes (501 KiB)

Extracting archive: sample_submission.7z
--
Path = sample_submission.7z
Type = 7z
Physical Size = 512684
Headers Size = 146
Method = LZMA2:6m
Solid = -
Blocks = 1

  0%    Everything is Ok

Size:       4280538
Compressed: 512684


In [ ]:
def load_test_file_set(test_file_path='./train/testing_list.txt'):
    #open the txt file containing the pathes of files that should be added to test dataset
    #convert the list to set datastructure
    test_files = open(test_file_path).read().splitlines()
    return set(test_files)

def load_validation_file_set(val_file_path='./train/validation_list.txt'):
    #open the txt file containing the pathes of files that should be added to validation dataset
    #convert the list to set datastructure
    validation_files = open(val_file_path).read().splitlines()
    return set(validation_files)

def is_test_file(test_set, file_path):
    return file_path in test_set

def is_validation_file(val_set, file_path):
    return file_path in val_set

In [ ]:
%cd /kaggle/working/
! mv ./train/audio/_background_noise_/README.md .

/kaggle/working


In [ ]:
X_train = []
Y_train = []

X_val   = []
Y_val   = []
X_test  = []
Y_test  = []

training_files_pathes = []

Background_Noise = []
! rm -rf ./train/audio/silence
! mkdir ./train/audio/silence

def read_train_audio(folder_path='./train/audio', fraction_of_data=1):    
    global X_train, X_val, Y_train, Y_val, Background_Noise, training_files_pathes
    
    test_file_set = load_test_file_set()
    validation_file_set = load_validation_file_set()
    
    for label in os.listdir(folder_path): #loop on all folders in the audio folder
        dir_path = os.path.join(folder_path, label)
        if os.path.isfile(dir_path):#skip any files
            continue
        for filename in os.listdir(dir_path): #loop on all files in folder
            if label == '_background_noise_':
                full_file_path = os.path.join(dir_path, filename)
                audio = tfio.audio.AudioIOTensor(full_file_path).to_tensor().numpy()
                audio_len = audio.shape[0]
                to_remove = audio_len % 16000
                audio = audio[:-to_remove]
                Background_Noise.append(audio)
                
            else:
                full_file_path = os.path.join(dir_path, filename)
                if os.path.isdir(full_file_path):
                    continue
                file_rel_path = os.path.join(label, filename)
                if is_validation_file(validation_file_set, file_rel_path):
                    X_val.append(full_file_path)                    
                    Y_val.append(label)
                else:
                    X_train.append(full_file_path)                    
                    Y_train.append(label)

    Background_Noise = np.concatenate(Background_Noise, axis=0).reshape((-1, 16000, 1))
    from scipy.io.wavfile import write
    for i in range(len(Background_Noise)):
        samplerate = 16000
        fname = f'./train/audio/silence/silence{i}.wav'
        write(fname, samplerate, Background_Noise[i])
        if i % 3 == 0:
            for i in range(2):
                X_val.append(fname)
                Y_val.append('silence')
        else:
            # append several times to testing because homa 2olayelin
            for i in range(8):
                X_train.append(fname)
                Y_train.append('silence')


# to use all data read_train_audio(fraction_of_data=1)
read_train_audio()

In [ ]:
from sklearn import preprocessing

label_encoder = preprocessing.LabelEncoder()

def encode_strings():
    global label_encoder, Y_train, Y_val
    label_encoder.fit(Y_train)
    print('classes : ', list(label_encoder.classes_))
    Y_train = label_encoder.transform(Y_train)
    Y_val = label_encoder.transform(Y_val)
    
encode_strings()


classes :  ['bed', 'bird', 'cat', 'dog', 'down', 'eight', 'five', 'four', 'go', 'happy', 'house', 'left', 'marvin', 'nine', 'no', 'off', 'on', 'one', 'right', 'seven', 'sheila', 'silence', 'six', 'stop', 'three', 'tree', 'two', 'up', 'wow', 'yes', 'zero']


In [ ]:
print(label_encoder.transform(['bed']))
print(label_encoder.transform(['dog']))
print(label_encoder.transform(['four']))
print(label_encoder.transform(['right']))

[0]
[3]
[7]
[18]


In [ ]:
# ! 7z x test.7z -o./test


7-Zip [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,2 CPUs Intel(R) Xeon(R) CPU @ 2.30GHz (306F0),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 2640679130 bytes (2519 MiB)

Extracting archive: test.7z
--
Path = test.7z
Type = 7z
Physical Size = 2640679130
Headers Size = 1345163
Method = Delta LZMA2:24
Solid = +
Blocks = 3

  0%      0% 133 - test/audio/clip_0033aedac.wav                                          0% 289 - test/audio/clip_0076547ba.wav                                          0% 443 - test/audio/clip_00c2578c8.wav                                          0% 591 - test/audio/clip_01093cc29.wav

In [ ]:
! cp -r /content/drive/'My Drive'/my_model .
! ls
classes =  ['bed', 'bird', 'cat', 'dog', 'down', 'eight', 'five', 'four', 'go', 'happy', 'house', 'left', 'marvin', 'nine', 'no', 'off', 'on', 'one', 'right', 'seven', 'sheila', 'silence', 'six', 'stop', 'three', 'tree', 'two', 'up', 'wow', 'yes', 'zero']
print(len(classes))
model = keras.models.load_model("my_model")

model.compile(loss=losses.sparse_categorical_crossentropy,
              optimizer='adam',
              metrics=['acc'])

cp: cannot stat '/content/drive/My Drive/my_model': No such file or directory
README.md  train
31


OSError: ignored

In [ ]:
# X_test = open("./testing_files.txt").read().splitlines()
# Y_test = []
# dirname = "./test/test/audio/"
# counter = 0
# print(len(X_test))
# for filename in X_test:
#   x = np.zeros(shape=(1, 16000, 1))
#   audio = tfio.audio.AudioIOTensor(dirname + filename).to_tensor().numpy().reshape((-1, 1))
#   x[0, 0:len(audio)] = audio
#   Y_test.append(np.argmax(model.predict(x)))a
#   counter += 1
#   if counter % 200 == 0:
#       print(counter)

75451
200
400
600
800
1000
1200
1400
1600
1800
2000
2200
2400
2600
2800
3000
3200
3400
3600
3800
4000
4200
4400
4600
4800
5000
5200
5400
5600
5800
6000
6200
6400
6600
6800
7000
7200
7400
7600
7800
8000
8200
8400
8600
8800
9000
9200
9400
9600
9800
10000
10200
10400
10600
10800
11000
11200
11400
11600
11800
12000
12200
12400
12600
12800
13000
13200
13400
13600
13800
14000
14200
14400
14600
14800
15000
15200
15400
15600
15800
16000
16200
16400
16600
16800
17000
17200
17400
17600
17800
18000
18200
18400
18600
18800
19000
19200
19400
19600
19800
20000
20200
20400
20600
20800
21000
21200
21400
21600
21800
22000
22200
22400
22600
22800
23000
23200
23400
23600
23800
24000
24200
24400
24600
24800
25000
25200
25400
25600
25800
26000
26200
26400
26600
26800
27000
27200
27400
27600
27800
28000
28200
28400
28600
28800
29000
29200
29400
29600
29800
30000
30200
30400
30600
30800
31000
31200
31400
31600
31800
32000
32200
32400
32600
32800
33000
33200
33400
33600
33800
34000
34200
34400
34600
34800
350

In [ ]:
import csv
with open('submission.csv', 'w', newline='') as file:
  writer = csv.writer(file)
  writer.writerow(["fname", "label"])
  for i in range(len(X_test)):
    writer.writerow([X_test[i], Y_test[i]])

In [ ]:
# from google.colab import files
# files.download('submission.csv') 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
! pwd
! cp /content/submission.csv /kaggle/working
import csv
l = []
with open('submission.csv', newline='') as csvfile:
    csvreader = csv.reader(csvfile)
    l = [row for row in csvreader]

/kaggle/working


In [ ]:
known = ["yes", "no", "up", "down", "left", "right", "on", "off", "stop", "go", "silence"] # "unknown" not included
m = {}
for c in known:
  m[label_encoder.transform([c])[0]] = c


{4: 'down',
 8: 'go',
 11: 'left',
 14: 'no',
 15: 'off',
 16: 'on',
 18: 'right',
 21: 'silence',
 23: 'stop',
 27: 'up',
 29: 'yes'}

In [ ]:
with open('newsubmission.csv', 'w', newline='') as file:
  writer = csv.writer(file)
  writer.writerow(["fname", "label"])
  for i in range(1, len(l)):
    fname = l[i][0]
    num = int(l[i][1])
    if num in m:
      label = m[num]
    else:
      label = 'unknown'
    writer.writerow([fname, label])